In [1]:

from network.softNet import softNet
import torch
import trimesh
import os
from pytorch3d.structures import Meshes
import mano
from utils import utils_loss
os.environ['CUDA_VISIBLE_DEVICES'] = '0'
softnet = softNet()
checkpoint = torch.load("/home/zhaozhe/Pycode/NIPS24/soft/lightningv6/lightning_logs/version_21/checkpoints/epoch=202-step=97237.ckpt", map_location=torch.device('cpu'))['state_dict']
softnet.load_state_dict(checkpoint)
softnet.eval()
softnet = softnet.to('cuda')
from scipy.linalg import orthogonal_procrustes
from datasets import utils_HO3D_FPHA
import numpy as np
import json
id =0
def align_w_scale(mtx1, mtx2, return_trafo=False):
    """ Align the predicted entity in some optimality sense with the ground truth. """
    # center
    t1 = mtx1.mean(0)
    t2 = mtx2.mean(0)
    mtx1_t = mtx1 - t1
    mtx2_t = mtx2 - t2

    # scale
    s1 = np.linalg.norm(mtx1_t) + 1e-8
    mtx1_t /= s1
    s2 = np.linalg.norm(mtx2_t) + 1e-8
    mtx2_t /= s2

    # orth alignment
    R, s = orthogonal_procrustes(mtx1_t, mtx2_t)

    # apply trafos to the second matrix
    mtx2_t = np.dot(mtx2_t, R.T) * s
    mtx2_t = mtx2_t * s1 + t1
    if return_trafo:
        #return R, s, s1, t1 - t2
        return R, s, s1, t1 , t2 , s2    
    else:
        return mtx2_t




/home/zhaozhe/miniconda3/envs/pointcept/lib/python3.8/site-packages/requests/__init__.py:109: RequestsDependencyWarning: urllib3 (2.2.1) or chardet (None)/charset_normalizer (3.3.2) doesn't match a supported version!
  warnings.warn(


In [21]:
    test_id = 0
    object_names = ['12_pig.ply',
    '11_dog.ply',
    '10_chicken.ply',
    '09_monkey.ply',
    '08_sheep.ply',
    '07_horse.ply',
    '06_snake.ply',
    '05_dragon.ply',
    '04_rabbit.ply',
    '03_tiger.ply',
    '02_cow.ply',
    '01_mouse.ply',
    ]
    obj_pc_dict, obj_face_dict, obj_scale_dict, obj_pc_resample_dict, obj_resample_faceid_dict = utils_HO3D_FPHA.load_objects_HMDO()
    diverse_grasp_result = json.load(open('./diverse_grasp/HMDO/obj_id_{}.json'.format(test_id)))
    recon_params = diverse_grasp_result['recon_params']  # list of predicted MANO params
    R_list = diverse_grasp_result['R_list']          # list of Random Rotation MATRIX for rotating the object, in so(3)
    r_list = diverse_grasp_result['r_list']          # list of Random Rotation ANGLES for rotating the object, in R^(3)
    trans_list = diverse_grasp_result['trans_list']  # list of Random Translation for translating the object, in R^(3)
    # change the mano layer here
    with torch.no_grad():
        rh_mano = mano.load(model_path='./models/mano/MANO_RIGHT.pkl',
                            model_type='mano',
                            use_pca=True,
                            num_pca_comps=45,
                            batch_size=1,
                            flat_hand_mean=True)
    rh_faces = torch.from_numpy(rh_mano.faces.astype(np.int32)).view(1, -1, 3)  # [1, 1538, 3], face triangle indexes
    rh_mano.eval()
    meshes_all = []
    # load object mesh
    #obj_name = mapping_obj_name(obj_id)
    obj_xyz_origin = np.array(obj_pc_dict[object_names[test_id]])
    obj_face_origin = np.array(obj_face_dict[object_names[test_id]])
    mean_xyz_obj = torch.tensor(obj_xyz_origin).mean(dim=(0))
    print(mean_xyz_obj)
    obj_mesh = trimesh.Trimesh(vertices=obj_xyz_origin, faces=obj_face_origin)#,
                               #face_colors=[240,128,128])
    for i in range(id,id+1):#len(recon_params)):  # 100 is the number of generated grasps
        recon_param = np.array(recon_params[i])
        recon_param = torch.tensor(recon_param, dtype=torch.float32)  # [1, 61]
        R = np.array(R_list[i])
        trans = np.array(trans_list[i])
        r = np.array(r_list[i])
        
        # hand mesh
        pred_mano = rh_mano(betas=recon_param[:, :10],
                            global_orient=recon_param[:, 10:13],
                            hand_pose=recon_param[:, 13:58],
                            transl=recon_param[:, 58:])
        hand_verts = pred_mano.vertices

        hand_verts = hand_verts.detach().squeeze(0).numpy()  # [778,3]
        recon_xyz = np.matmul(np.linalg.inv(R[:3, :3]), (hand_verts - R[:3, 3].reshape(1, -1)).T).T
        hand_mesh = trimesh.Trimesh(vertices=recon_xyz, faces=rh_faces.numpy().reshape((-1, 3)),
                                    face_colors=[int(0.85882353*255), int(0.74117647*255), int(0.65098039*255)])

        # vis current affordance
        #
        #trimesh.Scene(meshes).show()
        meshes_all.append(hand_mesh)
#trimesh.Scene(meshes).show()
    # vis all affordance
meshes = [hand_mesh, obj_mesh]
meshes_all.append(obj_mesh)
id+=1
trimesh.Scene(meshes).show()


tensor([-1.0475e-10, -3.2951e-10, -3.2225e-10], dtype=torch.float64)


In [19]:

with torch.no_grad():
    rh_mano = mano.load(model_path='./models/mano/MANO_RIGHT.pkl',
                                model_type='mano',
                                use_pca=False,
                                num_pca_comps=51,
                                batch_size=1,
                                flat_hand_mean=True)
rh_faces = torch.from_numpy(rh_mano.faces.astype(np.int32)).view(1, -1, 3).contiguous() # [1, 1538, 3], face triangle indexes    


mesh = obj_mesh
move = np.array([-0.0258,  0.0053, -0.6903])*0
#, face_id = trimesh.sample.sample_surface(object_full,3000)
hand_mesh = hand_mesh

hand_mesh.vertices = hand_mesh.vertices + move
obj_mesh.vertices = obj_mesh.vertices + move
hand_vertices = hand_mesh.vertices#$, face_id =  trimesh.sample.sample_surface(hand_mesh, 1000)
object_vertices = obj_mesh.vertices #, face_id =  trimesh.sample.sample_surface(object_vertices_full, 3000)

#hand_mesh.vertices = hand_mesh.vertices/scale
prior_idx=[
          697, 698, 699, 700, 712, 713, 714, 715, 737, 738, 739, 740, 741, 743, 744, 745, 746, 748, 749,
          750, 753, 754, 755, 756, 757, 758, 759, 760, 761, 762, 763, 764, 765, 766, 767, 768,
          46, 47, 48, 49, 164, 165, 166, 167, 194, 195, 223, 237, 238, 280, 281, 298, 301, 317, 320, 323, 324, 325, 326,
          327, 328, 329, 330, 331, 332, 333, 340, 341, 342, 343, 344, 345, 346, 347, 348, 349, 350, 351, 352, 353, 354,
          355,
          356, 357, 358, 359, 375, 376, 386, 387, 396, 397, 402, 403, 413, 429, 433, 434, 435, 436, 437, 438,
          439, 440, 441, 442, 443, 444, 452, 453, 454, 455, 456, 459, 460, 461, 462, 463, 464, 465, 466, 467,
          468, 469, 470, 471, 484, 485, 486, 496, 497, 506, 507, 513, 514, 524, 545, 546, 547, 548, 549,
          550, 551, 552, 553, 555, 563, 564, 565, 566, 567, 570, 572, 573, 574, 575, 576, 577, 578,
          580, 581, 582, 583, 600, 601, 602, 614, 615, 624, 625, 630, 631, 641, 663, 664, 665, 666, 667,
          668, 670, 672, 680, 681, 682, 683, 684, 686, 687, 688, 689, 690, 691, 692, 693, 694, 695,
          73, 96, 98, 99, 772, 774, 775, 777
          ]
hand_vertices =  torch.tensor(hand_vertices).unsqueeze(0)
mesh_ = Meshes(verts= hand_vertices, faces=rh_faces)
hand_normal = mesh_.verts_normals_packed().view(-1, 778, 3)
hand_normal_prior = hand_normal[0][prior_idx].unsqueeze(0)
#object_vertices_org = align_w_scale(object_vertices,object_vertices_org)
#R, s, s1, t1 , t2 , s2 = align_w_scale(object_vertices_full,object_full,return_trafo = True)
#object_vertices_org = np.dot((object_vertices_org - t2)/s2, R.T) * s* s1 + t1
mesh#.vertices = object_vertices_org
hand_vertices_prior = torch.tensor(hand_vertices[0][prior_idx]).float().unsqueeze(0)
obj_nn_dist_recon, obj_nn_idx_recon = utils_loss.get_NN(torch.tensor(object_vertices).unsqueeze(0).float(), hand_vertices_prior)
interior = utils_loss.get_interior(hand_normal_prior, hand_vertices_prior, torch.tensor(object_vertices).unsqueeze(0).float(), obj_nn_idx_recon).type(torch.bool)
#interior = interior。float
contact_map_bool = (obj_nn_dist_recon<1e-4).float()
obj_nn_dist_recon[interior]= obj_nn_dist_recon[interior]*-1
contact_map = obj_nn_dist_recon
contact_map_bool[interior] = (contact_map_bool[interior]*-1).float()
contact_map = contact_map *abs(contact_map_bool)
print(contact_map_bool.sum())
print(contact_map.size())
data_dict = {}

print(torch.tensor(object_vertices).size())
mesh_obj = Meshes(verts= torch.tensor(object_vertices).unsqueeze(0), faces=torch.tensor(mesh.faces).unsqueeze(0))
gt_normal = mesh_obj.verts_normals_packed()#.view(-1, 778, 3)
print(gt_normal.size())
data_dict['grid_size'] = torch.tensor([0.001]).float().cuda()
data_dict['offset'] = torch.tensor([torch.tensor(object_vertices).size(0)]).cuda()

data_dict['coord'] = torch.tensor(object_vertices).float().cuda()
data_dict['feat'] = torch.cat((contact_map_bool.unsqueeze(2),contact_map.unsqueeze(2),gt_normal.unsqueeze(0)),dim=2).squeeze(0).cuda().float()
print(data_dict['feat'].size())
print(data_dict['coord'].size())
print(data_dict['offset'])
print( torch.tensor(object_vertices).size())
hand_mesh = trimesh.Trimesh(vertices=hand_vertices.squeeze(0).detach().cpu().numpy(), faces=rh_faces.detach().cpu().numpy().reshape((-1, 3)),face_colors=[int(0.85882353*255), int(0.74117647*255), int(0.65098039*255)])

object_pred ,movement,_= softnet(data_dict)
from pytorch3d.ops import taubin_smoothing
from pytorch3d.structures import Meshes
verts=[object_pred.squeeze(0).to('cuda')]
#faces=[face[0]]
face = [torch.tensor(mesh.faces).to('cuda')]
pytorch3d_mesh = Meshes(verts,face)
pytorch3d_mesh = taubin_smoothing(meshes=pytorch3d_mesh, lambd=0.53, mu= -0.53, num_iter= 5)
mesh.vertices = pytorch3d_mesh.verts_list()[0].cpu().detach().numpy()
meshes = [mesh, hand_mesh]
trimesh.Scene(meshes).show()

tensor(318.)
torch.Size([1, 9740])
torch.Size([9740, 3])
torch.Size([9740, 3])
torch.Size([9740, 5])
torch.Size([9740, 3])
tensor([9740], device='cuda:0')
torch.Size([9740, 3])


/tmp/ipykernel_6065/759977320.py:44: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  hand_vertices_prior = torch.tensor(hand_vertices[0][prior_idx]).float().unsqueeze(0)


In [20]:

meshes = [mesh]
trimesh.Scene(meshes).show()

In [ ]:
mesh.vertices = object_pred.cpu().detach().numpy()
meshes = [mesh, hand_mesh]
trimesh.Scene(meshes).show()

In [ ]:
from pytorch3d.ops import taubin_smoothing
from pytorch3d.structures import Meshes
verts=[object_pred.squeeze(0).to('cuda')]
#faces=[face[0]]
face = [torch.tensor(mesh.faces).to('cuda')]
pytorch3d_mesh = Meshes(verts,face)
pytorch3d_mesh = taubin_smoothing(meshes=pytorch3d_mesh, lambd=0.53, mu= -0.53, num_iter= 5)
mesh.vertices = pytorch3d_mesh.verts_list()[0].cpu().detach().numpy()
meshes = [mesh, hand_mesh]
trimesh.Scene(meshes).show()

In [ ]:
meshes = [mesh]
trimesh.Scene(meshes).show()

In [ ]:
import trimesh
import numpy as np
import torch
import  os

object_full_org = trimesh.load("/data/zz/HMDO/sequence06/object_mesh/org.ply") 
centroid = object_full_org.vertices.mean(axis=0)
object_full_org.vertices-=centroid
object_full = trimesh.load("/data/zz/HMDO/sequence06/object_mesh/0041.ply") 

object_full.vertices = object_full_org.vertices

meshes = [object_full]
trimesh.Scene(meshes).show()
for mesh in sorted(os.listdir("/data/zz/HMDO/sequence06/object_mesh/")):
    object_full = trimesh.load("/data/zz/HMDO/sequence06/object_mesh/"+mesh) 
    print(torch.tensor(object_full.vertices).size(0))

8448
8448
8448
8448
8448
8448
8448
8448
8448
8451
8452
8453
8453
8455
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8456
8457
8457
8457
8456
8457
8457
8457
8457
8457
8457
8457
8457
8457
8457
8457
8457
8457
8457
8457
8457
8457
8457
8457
8457
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8462
8457
8458
8458
8458
8457
8458
8458
8458
8458
8458
8458
8458
8457
8458
8458
8457
8458
8458
8456
8455
8456
8455
8456
8456
8455
8456
8456
8455
8456
8456
8456
8455
8456
8455
8456
8456
8455
8456
8454
8454
8451
8451
8451
8451
8448
8448
8448
8451
8448
8448
8448
8448
8448


In [ ]:
object_full.export('/data/zz/HMDO/sequence06/object_mesh/org_mesh.ply')